In [91]:
import geopandas as gpd
import matplotlib.pyplot as plt
from shapely.geometry import Point, LinearRing, Polygon
import pandas as pd
import folium
from folium.plugins import FastMarkerCluster
from folium.plugins import HeatMap

In [92]:
 #abrindo o shapefile
 mun_sp_shp = gpd.read_file('C:/Users/T-Gamer/Documents/MeusProjetos/Roubo_Celulares/Python/Base/35MUE250GC_SIR.shp')

In [93]:
#filtrando a região metropolitana de São Paulo
gdf_sp = mun_sp_shp[mun_sp_shp['NM_MUNICIP'].isin(['ARUJÁ','BARUERI','BIRITIBA-MIRIM','CAIEIRAS','CAJAMAR','CARAPICUÍBA','COTIA','DIADEMA','EMBU','EMBU-GUAÇU','FERRAZ DE VASCONCELOS','FRANCISCO MORATO','FRANCO DA ROCHA','GUARAREMA','GUARULHOS','ITAPECERICA DA SERRA','ITAPEVI','ITAQUAQUECETUBA','JANDIRA','JUQUITIBA','MAIRIPORÃ','MAUÁ','MOGI DAS CRUZES','OSASCO','PIRAPORA DO BOM JESUS','POÁ','RIBEIRÃO PIRES','RIO GRANDE DA SERRA','SALESÓPOLIS','SANTA ISABEL','SANTANA DE PARNAÍBA','SANTO ANDRÉ','SÃO BERNARDO DO CAMPO','SÃO CAETANO DO SUL','SÃO LOURENÇO DA SERRA','SÃO PAULO','SUZANO','TABOÃO DA SERRA','VARGEM GRANDE PAULISTA'])]

In [94]:
#abrindo a base com os dados de roubos de celulares
filename = 'C:/Users/T-Gamer/Documents/MeusProjetos/Roubo_Celulares/Python/Base/dados_roubo_celular_sp_2020.xlsx'
df_roubos = pd.read_excel(filename)

In [95]:
#excluindo dados missing dos campos de latitude e longitude
df_roubos = df_roubos.dropna(subset=['LATITUDE', 'LONGITUDE'])

In [96]:
#adicionando a coluna geometry para transformar o dataframe (df) em geodataframe (gdf)
df_roubos['geometry'] = None
for index, row in df_roubos.iterrows():
    df_roubos.loc[index, 'geometry'] = Point(row.LONGITUDE, row.LATITUDE)

In [97]:
#transformando o df em gdf
gdf_roubos = gpd.GeoDataFrame(df_roubos, geometry = 'geometry')

In [119]:
#filtrando a região metropolitana de São Paulo
gdf_roubos_rmsp = gdf_roubos[gdf_roubos['CIDADE'].isin(['ARUJA','BARUERI','BIRITIBA-MIRIM','CAIEIRAS','CAJAMAR','CARAPICUIBA','COTIA','DIADEMA','EMBU','EMBU-GUAÇU','FERRAZ DE VASCONCELOS','FRANCISCO MORATO','FRANCO DA ROCHA','GUARAREMA','GUARULHOS','ITAPECERICA DA SERRA','ITAPEVI','ITAQUAQUECETUBA','JANDIRA','JUQUITIBA','MAIRIPORA','MAUA','MOGI DAS CRUZES','OSASCO','PIRAPORA DO BOM JESUS','POA','RIBEIRAO PIRES','RIO GRANDE DA SERRA','SALESOPOLIS','S.ISABEL','SANTANA DO PARNAIBA','S.ANDRE','S.BERNARDO DO CAMPO','S.CAETANO DO SUL','S.LOURENCO DA SERRA','S.PAULO','SUZANO','TABOAO DA SERRA','VARGEM GRANDE PAULISTA'])]

In [120]:
for index, municipio in gdf_sp.iterrows():
    qtd_roubos = len(gdf_roubos_rmsp[gdf_roubos_rmsp.intersects(municipio.geometry)])
    gdf_sp.loc[index, 'qtd_roubos'] = qtd_roubos

C:\Users\T-Gamer\AppData\Local\Programs\Python\Python39\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


In [122]:
#criando o mapa com folium
media_latitude = gdf_roubos_rmsp['LATITUDE'].mean()
media_longitude = gdf_roubos_rmsp['LONGITUDE'].mean()
fastmarker = FastMarkerCluster(gdf_roubos_rmsp[['LATITUDE','LONGITUDE']])
heatmap = HeatMap(gdf_roubos_rmsp[['LATITUDE', 'LONGITUDE']])
m = folium.Map(location=[media_latitude, media_longitude], tiles='cartodbpositron')
for _, municipio in gdf_sp.iterrows():
    limites = folium.features.GeoJson(municipio.geometry,
     style_function=lambda feature:{
        'color':'black',
        'weight':0.5,
        'fillOpacity':0.0
        })
    popup = folium.Popup('''
    Município: {} <br>
    Roubos registrados em Novembro:{}
    '''.format(municipio.NM_MUNICIP, str(int(municipio.qtd_roubos))),max_width = 300)
    popup.add_to(limites)
    limites.add_to(m)
m.add_child(fastmarker)
m.add_child(heatmap)
m.save('C:/Users/T-Gamer/Documents/MeusProjetos/Roubo_Celulares/Python/mapa_roubos.html')
m